# Magics, Imports, and Versions

In [ ]:
%reload_ext autoreload
%autoreload 2
%matplotlib inline

import csv
import json
import matplotlib.pyplot as plt
import numpy as np
import operator
from pathlib import Path
import PIL
import pyedflib
from scipy import signal
from subprocess import call
import sys
import typing
import urllib

import fastai
from fastai.vision import *
from fastai.callbacks.hooks import *
from fastai.utils.mem import *

In [2]:
print(f'__Python VERSION: {sys.version}')

try:
    print(f'__pyTorch VERSION: {torch.__version__}')
    PYTORCH = True
except: 
    print("Pytorch Not Installed")
    PYTORCH = False

try:
    print(f'__fastai VERSION: {fastai.__version__}')
except:
    print("fastai Not Installed")
    
print('__CUDA VERSION')

! nvcc --version

if PYTORCH:
    print(f'__CUDNN VERSION: {torch.backends.cudnn.version()}')
    print(f'__Number CUDA Devices: {torch.cuda.device_count()}')
    
print(f'__Devices')

try:
    call(["nvidia-smi", "--format=csv", "--query-gpu=index,name,driver_version,memory.total,memory.used,memory.free"])
    print(f'Active CUDA Device: GPU {torch.cuda.current_device()}')

    print (f'Available devices: {torch.cuda.device_count()}')
    print (f'Current cuda device {torch.cuda.current_device()}')
except:
    print("No GPUs Found")

__Python VERSION: 3.7.1 (default, Dec 14 2018, 19:28:38) 
[GCC 7.3.0]
__pyTorch VERSION: 1.0.1.post2
__fastai VERSION: 1.0.53.dev0
__CUDA VERSION
nvcc: NVIDIA (R) Cuda compiler driver
Copyright (c) 2005-2018 NVIDIA Corporation
Built on Sat_Aug_25_21:08:01_CDT_2018
Cuda compilation tools, release 10.0, V10.0.130
__CUDNN VERSION: 7402
__Number CUDA Devices: 1
__Devices
Active CUDA Device: GPU 0
Available devices: 1
Current cuda device 0


# Path and Dirs

In [ ]:
here = Path(f'{os.getcwd()}')
data_path = here.parent/'data'
raw_path = data_path/'raw'/'v1.5.0/edf'
with open(here.parent/'data_dict.json', 'r') as file:
     data_dict = json.load(file)
train_path = data_path/'augmented/train_val'
test_path = data_path/'augmented/test'

In [ ]:
def ensure_dir(directory):
    if not os.path.exists(directory):
        print(f'Creating {directory}')
        os.makedirs(directory)

In [3]:
ensure_dir(data_path/'images/test')
img_path = data_path/'images/test'

Creating /home/jupyter/tuh_eeg/data/images/test


In [4]:
# this is from 4 segments :0
len(test_path.ls())

195620

# Math Functions

In [5]:
def divergence(F):
    """ compute the divergence of n-D scalar field `F` """
    """ https://stackoverflow.com/questions/11435809/compute-divergence-of-vector-field-using-python """
    return reduce(np.add,np.gradient(F))

In [6]:
def scale(F):
    """ scale a n-D scalar field to [0-255] range for image creation """
    F *= (255.0/F.max())
    return F

In [7]:
def convolve_8NNavg(F):
    """ compute the average of the 8 nearest neighbors for each point in the n-D scalar field `F` """
    """ https://gis.stackexchange.com/questions/254753/calculate-the-average-of-neighbor-pixels-for-raster-edge """
    return scipy.ndimage.generic_filter(F, np.nanmean, size=3, mode='constant', cval=np.NaN)


# Test and Transform

In [ ]:
gp = test_path/'le_00004151_s002_d2007_09_28_t003_ts003_ch041_h96_w8_o75_st000422.0_et000430.0_p00212_tp00222.npy'

In [9]:
for file in test_path.ls():
    # if file == gp:
    data = np.load(file)
    save_loc = img_path/f'{file.stem}.png'
    S = np.fft.fft(data)
    D = divergence(S)
    S = abs(S)
    D = abs(D)
    I = convolve_8NNavg(D)
    S = scale(S)
    D = scale(D)
    I = scale(I)
    img = np.stack([S,D,I], axis=2)
    img = PIL.Image.fromarray(img, 'RGB')
    img = img.resize((224, 224), PIL.Image.ANTIALIAS)
    img.save(save_loc)
    #plt.imshow(np.asarray(img))

KeyboardInterrupt: 